# 🎆 ISMRM Raw Data


<h3>1️⃣ Shopping </h3>

## 👩‍🎤 NORAH JONES Readout

<br>
<center><code style="background:yellow;color:black"> We are looking at the readout block of our NORAH JONES sequence <code>/Sequence/CartesianReadout3D.spv</code>. If you are an OSX user, you can inspect sequence components using <a href="https://www.heartvista.ai/spinbench">SpinBench!</a></code></center>
<br>

![](../assets/sequence_order.gif)


We have **100 `acquisitions`** (or `TR`s or `Phase Encoding`s) that are ordered outside-in to sample the center of the k-space the latest (steady-state). At each **`acquisition`** we have **100 `samples`**. NORAH JONES sequence acquires all 4 images in this fashion, at the same location. You can see all the readout parameters below:


![](../assets/readout_params.png)

## NORAH JONES k-space in ISMRM-RD

![](../assets/ismrmrd_structure.png)

<h3> 2️⃣ Mise en place </h3>

Let's read and parse the data using `NumPy` relying purely on metadata provided by `python-ismrmrd`.

### Import ISMRM-RD modules 🧲

In [ ]:
from ismrmrd import Dataset as read_ismrmrd
from ismrmrd.xsd import CreateFromDocument as parse_ismrmd_header
import numpy as np
import plotly.express as px
import plotly.graph_objects as go

### Create a simple list storing file names 🗂

In [ ]:
files = list()
for chord in ['chord1','chord2','chord3','chord4']:
    files.append('../KSpace/sub-ismrm_ses-sunrise_acq-' + chord + '.h5')
files

###  Explore `acq-chord1` file 🕵️‍♀️

#### Read data & parse header

In [ ]:
# Read the first file to explore data
dset = read_ismrmrd(files[0], 'dataset')

# Parse header 
header = parse_ismrmd_header(dset.read_xml_header())

# See what's in the header
print('header has:',list(vars(header).keys()))
print('----')
print('header.encoding[0] has:',list(vars(header.encoding[0]).keys()))

#### Grab some useful metadata values

In [ ]:
nX = header.encoding[0].encodedSpace.matrixSize.x
nY = header.encoding[0].encodedSpace.matrixSize.y
nZ = header.encoding[0].encodedSpace.matrixSize.z
nCoils = header.acquisitionSystemInformation.receiverChannels
print('nX: ', nX,'nY: ', nY,'nZ: ', nZ, 'nCoils: ', nCoils)

###  Initialize a 3D `NumPy` matrix to store multi-channel raw data 🗃

We already know the dimensions! Given that we expect complex data, we can set `dtype=complex64` 😎 For simplicity I will omit nZ (we have one slice). 

In [ ]:
raw = np.zeros((nCoils, nX, nY), dtype=np.complex64)
print('Raw data shape: ', raw.shape)

### Loop over `acquisitions` to fill out `raw` 

The `dset` object we created from the ISMRM-RD `Dataset` (we used alias `read_ismrmrd`) class has an important method: **`read_acquisition`**. We will loop over `nY` to read k-space stripes (cartesian) one by one.

In [ ]:
for tr in range(nY):
    raw[:,:,tr] = dset.read_acquisition(tr).data

#### Is not `Plotly` simply amazing? 
This feature has been introduced in `v4.14.0`: with a single line of code you can animate or grid display 3D data.

In [ ]:
fig = px.imshow(raw.real,animation_frame=0, color_continuous_scale='viridis', labels=dict(animation_frame="Channel"),template='plotly_dark')
fig.update_layout(title='Channel Raw')
fig

<h3> 3️⃣ Time to perform a modest reconstruction :) </h3></div>


In [ ]:
from scipy.fft import fft2, fftshift
from scipy import ndimage

#### Loop over channels and `fft2`

Tip: remove `fftshift` from `fourier_ellipsoid` function call, set filter size > `20`, then play the animation along with your remix from the first notebook 🎵🎶

In [ ]:
im = np.zeros(raw.shape)

# Let's apply some ellipsoid filter. 
raw = ndimage.fourier_ellipsoid(fftshift(raw),size=2)
#raw = ndimage.fourier_ellipsoid(raw,size=2)

for ch in range(nCoils):
    # Comment in and see what it gives 
    im[ch,:,:] = abs(fftshift(fft2(raw[ch,:,:])))
    # Normalize 
    im[ch,:,:] /= im[ch,:,:].max()

In [ ]:
fig = px.imshow(im,color_continuous_scale='viridis', animation_frame=0,template='plotly_dark')
fig.update_layout(title='Channel Recon').show()
fig

In [ ]:
im_sos = np.sqrt(np.sum(im*np.conj(im),axis=0))
# Normalize
im_sos /= im_sos.max()

# Crop a bit 
fig = px.imshow(im_sos[10:90,0:80],template='plotly_dark',color_continuous_scale='viridis')
fig.update_layout(title='Sum of Squares Combine')
fig

<div class="alert alert-block alert-warning">
<h3>  Exercises </h3></div>

* Rotate/flip images
* Reconstruct `SoS` images for every TR by writing some functions and collect them into a 3D matrix.
    * Display voxel intensity changes over TRs at the center of each (14) sphere 